# Section: Federated Learning

# Lesson: Introducing Federated Learning

Federated Learning is a technique for training Deep Learning models on data to which you do not have access. Basically:

Federated Learning: Instead of bringing all the data to one machine and training a model, we bring the model to the data, train it locally, and merely upload "model updates" to a central server.

Use Cases:

    - app company (Texting prediction app)
    - predictive maintenance (automobiles / industrial engines)
    - wearable medical devices
    - ad blockers / autotomplete in browsers (Firefox/Brave)
    
Challenge Description: data is distributed amongst sources but we cannot aggregated it because of:

    - privacy concerns: legal, user discomfort, competitive dynamics
    - engineering: the bandwidth/storage requirements of aggregating the larger dataset

# Lesson: Introducing / Installing PySyft

In order to perform Federated Learning, we need to be able to use Deep Learning techniques on remote machines. This will require a new set of tools. Specifically, we will use an extensin of PyTorch called PySyft.

### Install PySyft

The easiest way to install the required libraries is with [Conda](https://docs.conda.io/projects/conda/en/latest/user-guide/overview.html). Create a new environment, then install the dependencies in that environment. In your terminal:

```bash
conda create -n pysyft python=3
conda activate pysyft # some older version of conda require "source activate pysyft" instead.
conda install jupyter notebook
pip install syft
pip install numpy
```

If you have any errors relating to zstd - run the following (if everything above installed fine then skip this step):

```
pip install --upgrade --force-reinstall zstd
```

and then retry installing syft (pip install syft).

If you are using Windows, I suggest installing [Anaconda and using the Anaconda Prompt](https://docs.anaconda.com/anaconda/user-guide/getting-started/) to work from the command line. 

With this environment activated and in the repo directory, launch Jupyter Notebook:

```bash
jupyter notebook
```

and re-open this notebook on the new Jupyter server.

If any part of this doesn't work for you (or any of the tests fail) - first check the [README](https://github.com/OpenMined/PySyft.git) for installation help and then open a Github Issue or ping the #beginner channel in our slack! [slack.openmined.org](http://slack.openmined.org/)

In [1]:
import torch as th

In [ ]:
x = th.tensor([1,2,3,4,5])
x

In [ ]:
y = x + x

In [ ]:
print(y)

In [5]:
import syft as sy

W0820 00:00:27.779507 139706847606592 secure_random.py:26] Falling back to insecure randomness since the required custom op could not be found for the installed version of TensorFlow. Fix this by compiling custom ops. Missing file was '/usr/local/lib/python3.6/dist-packages/tf_encrypted/operations/secure_random/secure_random_module_tf_1.14.0.so'
W0820 00:00:27.802893 139706847606592 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/tf_encrypted/session.py:26: The name tf.Session is deprecated. Please use tf.compat.v1.Session instead.



In [6]:
hook = sy.TorchHook(th)

In [ ]:
th.tensor([1,2,3,4,5])

# Lesson: Basic Remote Execution in PySyft

## PySyft => Remote PyTorch

The essence of Federated Learning is the ability to train models in parallel on a wide number of machines. Thus, we need the ability to tell remote machines to execute the operations required for Deep Learning.

Thus, instead of using Torch tensors - we're now going to work with **pointers** to tensors. Let me show you what I mean. First, let's create a "pretend" machine owned by a "pretend" person - we'll call him Bob.

In [ ]:
bob = sy.VirtualWorker(hook, id="bob")

In [ ]:
bob._objects

In [ ]:
x = th.tensor([1,2,3,4,5])

In [ ]:
x = x.send(bob)

In [ ]:
bob._objects

In [ ]:
x.location

In [ ]:
x.id_at_location

In [ ]:
x.id

In [ ]:
x.owner

In [ ]:
hook.local_worker

In [ ]:
x

In [ ]:
x = x.get()
x

In [ ]:
bob._objects

# Project: Playing with Remote Tensors

In this project, I want you to .send() and .get() a tensor to TWO workers by calling .send(bob,alice). This will first require the creation of another VirtualWorker called alice.

In [ ]:
# try this project here!


bob.clear_objects, alice.clear_objects

In [ ]:
bob = sy.VirtualWorker(hook, id="bob")
alice = sy.VirtualWorker(hook, id="alice")

In [ ]:
y = th.tensor([1,3,45,3])

In [ ]:
y = y.send(bob, alice)

In [ ]:
bob._objects, alice._objects

In [ ]:
y

In [ ]:
y.id

In [ ]:
y = y.get()
y

# Lesson: Introducing Remote Arithmetic

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)
y = th.tensor([1,1,1,1,1]).send(bob)

In [ ]:
x

In [ ]:
y

In [ ]:
z = x + y

In [ ]:
z

In [ ]:
z = z.get()
z

In [ ]:
z = th.add(x,y)
z

In [ ]:
z = z.get()
z

In [ ]:
x = th.tensor([1.,2,3,4,5], requires_grad=True).send(bob)
y = th.tensor([1.,1,1,1,1], requires_grad=True).send(bob)

In [ ]:
z = (x + y).sum()

In [ ]:
z.backward()

In [ ]:
x = x.get()

In [ ]:
x

In [ ]:
x.grad

# Project: Learn a Simple Linear Model

In this project, I'd like for you to create a simple linear model which will solve for the following dataset below. You should use only Variables and .backward() to do so (no optimizers or nn.Modules). Furthermore, you must do so with both the data and the model being located on Bob's machine.

In [ ]:
# try this project here!
bob = sy.VirtualWorker(hook, id = "bob")
x = th.tensor([[1.,1],[0,1], [1,0], [0,0]], requires_grad=True).send(bob)
y = th.tensor([[1.],[1],[0],[0]],requires_grad=True).send(bob)

In [ ]:
weights = th.tensor([[0.],[0.]],requires_grad = True).send(bob)

In [ ]:
for i in range(10):
    pred = x.mm(weights)
    loss = ((pred - y)**2).sum()
    loss.backward()
    
    weights.data.sub_(weights.grad * 0.1)
    weights.grad *= 0
    
    print(loss.get().data)
    

# Lesson: Garbage Collection and Common Errors


In [ ]:
bob = bob.clear_objects()

In [ ]:
bob._objects

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)

In [ ]:
bob._objects

In [ ]:
del x

In [ ]:
bob._objects

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)

In [ ]:
bob._objects

In [ ]:
x = "asdf"

In [ ]:
bob._objects

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)

In [ ]:
x

In [ ]:
bob._objects

In [ ]:
x = "asdf"

In [ ]:
bob._objects

In [ ]:
del x

In [ ]:
bob._objects

In [ ]:
bob = bob.clear_objects()
bob._objects

In [ ]:
for i in range(1000):
    x = th.tensor([1,2,3,4,5]).send(bob)

In [ ]:
bob._objects

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)
y = th.tensor([1,1,1,1,1])

In [ ]:
z = x + y

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)
y = th.tensor([1,1,1,1,1]).send(alice)

In [ ]:
z = x + y

# Lesson: Toy Federated Learning

Let's start by training a toy model the centralized way. This is about a simple as models get. We first need:

- a toy dataset
- a model
- some basic training logic for training a model to fit the data.

In [ ]:
from torch import nn, optim

In [ ]:
# A Toy Dataset
data = th.tensor([[1.,1],[0,1],[1,0],[0,0]], requires_grad=True)
target = th.tensor([[1.],[1], [0], [0]], requires_grad=True)

In [ ]:
# A Toy Model
model = nn.Linear(2,1)

In [ ]:
opt = optim.SGD(params=model.parameters(), lr=0.1)

In [ ]:
def train(iterations=20):
    for iter in range(iterations):
        opt.zero_grad()

        pred = model(data)

        loss = ((pred - target)**2).sum()

        loss.backward()

        opt.step()

        print(loss.data)
        
train()

In [ ]:
data_bob = data[0:2].send(bob)
target_bob = target[0:2].send(bob)

In [ ]:
data_alice = data[2:4].send(alice)
target_alice = target[2:4].send(alice)

In [ ]:
datasets = [(data_bob, target_bob), (data_alice, target_alice)]

In [ ]:
def train(iterations=20):

    model = nn.Linear(2,1)
    opt = optim.SGD(params=model.parameters(), lr=0.1)
    
    for iter in range(iterations):

        for _data, _target in datasets:

            # send model to the data
            model = model.send(_data.location)

            # do normal training
            opt.zero_grad()
            pred = model(_data)
            loss = ((pred - _target)**2).sum()
            loss.backward()
            opt.step()

            # get smarter model back
            model = model.get()

            print(loss.get())

In [ ]:
train()

# Lesson: Advanced Remote Execution Tools

In the last section we trained a toy model using Federated Learning. We did this by calling .send() and .get() on our model, sending it to the location of training data, updating it, and then bringing it back. However, at the end of the example we realized that we needed to go a bit further to protect people privacy. Namely, we want to average the gradients BEFORE calling .get(). That way, we won't ever see anyone's exact gradient (thus better protecting their privacy!!!)

But, in order to do this, we need a few more pieces:

- use a pointer to send a Tensor directly to another worker

And in addition, while we're here, we're going to learn about a few more advanced tensor operations as well which will help us both with this example and a few in the future!

In [ ]:
bob.clear_objects()
alice.clear_objects()

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)

In [ ]:
x = x.send(alice)

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
y = x + x

In [ ]:
y

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
jon = sy.VirtualWorker(hook, id="jon")

In [ ]:
bob.clear_objects()
alice.clear_objects()

x = th.tensor([1,2,3,4,5]).send(bob).send(alice)

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
x = x.get()
x

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
x = x.get()
x

In [ ]:
bob._objects

In [ ]:
bob.clear_objects()
alice.clear_objects()

x = th.tensor([1,2,3,4,5]).send(bob).send(alice)

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
del x

In [ ]:
bob._objects

In [ ]:
alice._objects

# Lesson: Pointer Chain Operations

In [ ]:
bob.clear_objects()
alice.clear_objects()

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob)

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
x.move(alice)

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
x = th.tensor([1,2,3,4,5]).send(bob).send(alice)

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
x.remote_get()

In [ ]:
bob._objects

In [ ]:
alice._objects

In [ ]:
x.move(bob)

In [ ]:
x

In [ ]:
bob._objects

In [ ]:
alice._objects

# Project 
For the final project for this section, you're going to train on the MNIST dataset using federated learning However the gradient should not come up to central server in raw form

In [2]:
import torchvision.datasets as datasets
from torchvision import transforms
transform = transforms.Compose([transforms.ToTensor(),
                                transforms.Normalize((0.5,), (0.5,)),])
mnist_trn = datasets.MNIST(root='./data_', train=True, download=True, transform=transform)
mnist_val = datasets.MNIST(root='./data_', train=False, download=True, transform=transform)

In [3]:
# Hyperparameters
bs = 64
classes = 10
input_dim = 784
H = 256
epochs = 10

In [4]:
model = th.nn.Sequential(
        th.nn.Linear(input_dim, H),
        th.nn.ReLU(),
        th.nn.Linear(H,H),
        th.nn.ReLU(),
        th.nn.Linear(H,classes),
        th.nn.LogSoftmax(dim=1),)

In [30]:
for i in model.parameters():
    with th.no_grad():
        print(i)
        print(i.set_(i))
    break

Parameter containing:
tensor([[ 0.0269, -0.0201,  0.0319,  ..., -0.0144, -0.0321,  0.0341],
        [-0.0301,  0.0294,  0.0289,  ...,  0.0120, -0.0047,  0.0352],
        [ 0.0104,  0.0327, -0.0186,  ...,  0.0195,  0.0180,  0.0269],
        ...,
        [ 0.0220,  0.0045,  0.0075,  ..., -0.0094, -0.0279, -0.0162],
        [ 0.0160,  0.0110,  0.0037,  ..., -0.0213, -0.0289,  0.0214],
        [ 0.0325,  0.0028, -0.0110,  ...,  0.0221, -0.0193, -0.0193]],
       requires_grad=True)
Parameter containing:
tensor([[ 0.0269, -0.0201,  0.0319,  ..., -0.0144, -0.0321,  0.0341],
        [-0.0301,  0.0294,  0.0289,  ...,  0.0120, -0.0047,  0.0352],
        [ 0.0104,  0.0327, -0.0186,  ...,  0.0195,  0.0180,  0.0269],
        ...,
        [ 0.0220,  0.0045,  0.0075,  ..., -0.0094, -0.0279, -0.0162],
        [ 0.0160,  0.0110,  0.0037,  ..., -0.0213, -0.0289,  0.0214],
        [ 0.0325,  0.0028, -0.0110,  ...,  0.0221, -0.0193, -0.0193]],
       requires_grad=True)


In [7]:
bob = sy.VirtualWorker(hook, id ="bob")
alice = sy.VirtualWorker(hook, id="alice")
grads_ = sy.VirtualWorker(hook, id ="grads")
bob.clear_objects
alice.clear_objects
grads_.clear_objects

<bound method ObjectStorage.clear_objects of <VirtualWorker id:grads #objects:0>>

In [9]:
bob._objects

{}

In [50]:
# del trn_bob, trn_alice, val_bob, val_alice

NameError: name 'trn_bob' is not defined

In [8]:
# data splits
trn_bob = sy.BaseDataset(mnist_trn.data[0:30000], mnist_trn.targets[0:30000]).send(bob)
trn_alice = sy.BaseDataset(mnist_trn.data[30000:],mnist_trn.targets[30000:]).send(alice)

val_bob = sy.BaseDataset(mnist_val.data[0:5000], mnist_val.targets[0:5000]).send(bob)
val_alice = sy.BaseDataset(mnist_val.data[5000:],mnist_val.data[5000:]).send(alice)


# Creating federated datasets, an extension of Pytorch TensorDataset class
federated_train_dataset = sy.FederatedDataset([trn_bob, trn_alice])
federated_test_dataset = sy.FederatedDataset([val_bob, val_alice])

# Creating federated dataloaders, an extension of Pytorch DataLoader class
federated_train_loader = sy.FederatedDataLoader(federated_train_dataset, 
                                                shuffle=True, batch_size=bs)
federated_test_loader = sy.FederatedDataLoader(federated_test_dataset, 
                                               shuffle=False, batch_size=bs)

In [189]:
# for x, y in federated_train_loader:
#     print(x.location.id)

bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob
bob


In [9]:
crit_bob = th.nn.NLLLoss()
crit_alice = th.nn.NLLLoss()
opt_bob = th.optim.Adam(model.parameters(), lr = 1e-3) 
opt_alice = th.optim.Adam(model.parameters(), lr = 1e-3)

In [133]:
import pdb


In [51]:
del model

In [36]:
get_ws_bs(model, model)

[tensor([[ 0.0269, -0.0201,  0.0319,  ..., -0.0144, -0.0321,  0.0341],
         [-0.0301,  0.0294,  0.0289,  ...,  0.0120, -0.0047,  0.0352],
         [ 0.0104,  0.0327, -0.0186,  ...,  0.0195,  0.0180,  0.0269],
         ...,
         [ 0.0220,  0.0045,  0.0075,  ..., -0.0094, -0.0279, -0.0162],
         [ 0.0160,  0.0110,  0.0037,  ..., -0.0213, -0.0289,  0.0214],
         [ 0.0325,  0.0028, -0.0110,  ...,  0.0221, -0.0193, -0.0193]],
        grad_fn=<DivBackward0>),
 tensor([ 3.2318e-02,  2.3415e-02, -2.0214e-03, -2.0372e-02, -2.0327e-02,
         -8.6619e-03,  2.4932e-02,  2.0776e-02,  9.3436e-03, -1.9919e-02,
          2.0594e-02,  3.9473e-03,  2.4405e-02, -1.4986e-02, -1.8181e-02,
          3.3454e-02, -1.1902e-02,  2.4144e-02,  5.3993e-03, -1.2691e-02,
         -2.5166e-02,  3.0923e-02, -5.9547e-03, -1.2756e-02, -3.2886e-02,
         -2.5562e-02,  1.5153e-02, -5.1027e-03,  1.1444e-02, -9.6117e-03,
          2.6991e-03,  1.7644e-02,  2.2871e-02, -1.3424e-02, -2.7068e-02,
        

In [13]:
def get_ws_bs(model_bob,model_alice):
    avg_ws_bs = []
    for m_1,m_2 in zip(model_bob.named_parameters(), model_alice.named_parameters()):
        m_1 = m_1.get()
        m_2 = m_2.get()
        avg_ws_bs += [((m_1[1] + m_2[1])/2)]
    
    return avg_ws_bs

def set_ws_bs(model, model_bob, model_alice):
    avg_ws_bs = get_ws_bs(model_bob, model_alice)
    with th.no_grad():
        for i, parameter in enumerate(model.parameters()):
            parameter.set_(avg_ws_bs[i].get())
    
    return model

In [14]:
import matplotlib.pyplot as plt
def fit(model, iterations = 2):
    model.train()
    models = list()
    for j in range(iterations):
        for i, (x, y) in enumerate(federated_train_loader):
#             pdb.set_trace()
            x = x.view(x.shape[0],-1)
            
            # do normal training
            if (x.location.id == 'bob'):
                model_bob = model.copy().send(x.location.id)
                opt_bob.zero_grad()
                pred_bob = model_bob(x.float())
                loss_bob = crit_bob(pred_bob, y)
                loss_bob.backward()
                opt_bob.step() 
                if i % 1000 == 0:
                    print("Bob's_loss: ", str(loss_bob.get().data))
                model_bob.move(grads_)
                      
            else:
                model_alice = model.copy().send(x.location.id)
                opt_alice.zero_grad()
                pred_alice = model_bob(x.float())
                loss_alice = crit_alice(pred_alice, y)
                loss_alice.backward()
                opt_alice.step()
                if i % 1000 == 0:
                    print("Alice's_loss: ", str(loss_alice.get().data))
                model_alice.move(grads_)
            # get smarter model back
    
    
    model = set_ws_bs(model ,model_bob, model_alice)
    
    return model  

In [ ]:
model = fit(model)

Bob's_loss:  tensor(9.4789)


Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:83856937649 -> alice:64574064469]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:74533167565 -> alice:40369079782]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:58423477464 -> alice:63030403952]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:3064617519 -> alice:53356612765]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 124

...

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:36567175809 -> alice:79068789129]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:93720720059 -> alice:50764203093]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:22204466642 -> alice:87832879838]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Exception ignored in: <bound method ObjectPointer.__del__ of [PointerTensor | me:57067601343 -> alice:17297788346]>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/syft/frameworks/torch/pointers/object_pointer.py", line 219, in __del__
    self.owner.send_msg(MSGTYPE.FORCE_OBJ_DEL, self.id_at_location, self.location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 229, in send_msg
    bin_response = self._send_msg(bin_message, location)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 10, in _send_msg
    return location._recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/virtual.py", line 13, in _recv_msg
    return self.recv_msg(message)
  File "/usr/local/lib/python3.6/dist-packages/syft/workers/base.py", line 263, in recv_msg
    response = self._message_router[msg_type](contents)
  File "/usr/local/lib/python3.6/dist-packages/syft/generic/object_storage.py", line 12

Bob's_loss:  tensor(10.2503)


In [40]:
model

Sequential(
  (0): Linear(in_features=784, out_features=256, bias=True)
  (1): ReLU()
  (2): Linear(in_features=256, out_features=256, bias=True)
  (3): ReLU()
  (4): Linear(in_features=256, out_features=10, bias=True)
  (5): LogSoftmax()
)

In [27]:
tra

True